In [1]:
import bokeh
bokeh.__version__

'1.4.0'

In [2]:
import xarray as xr
xr.__version__

'0.14.0'

# Open example RADOLAN-RW NetCDF

RADOLAN-RW data is made available by the German Meteorological Service (DWD) as hourly binary files at
https://opendata.dwd.de/climate_environment/CDC/grids_germany/hourly/radolan/historical/bin/

More info can be found here
https://www.dwd.de/DE/leistungen/radolan/radolan.html

At KIT we store all RADOALN-RW data as NetCDFs using a converter from RADOLAN-bin format to NetCDF https://github.com/cchwala/radolan_to_netcdf

Here we will use a data subsets of one day, 2016-06-08, where a small flooding event at the Ammer river in the village of Peißenberg occured.

In [3]:
ds = xr.open_dataset('radolan_rw_example_20160608.nc')
ds

<xarray.Dataset>
Dimensions:          (time: 48, x: 900, y: 900)
Coordinates:
  * x                (x) float64 -523.5 -522.5 -521.5 ... 373.5 374.5 375.5
  * y                (y) float64 -4.659e+03 -4.658e+03 ... -3.761e+03 -3.76e+03
    latitudes        (y, x) float64 ...
    longitudes       (y, x) float64 ...
  * time             (time) datetime64[ns] 2016-06-08T00:50:00 ... 2016-06-09T23:50:00
Data variables:
    rainfall_amount  (time, y, x) float32 ...
    radolan_grid     float64 ...
Attributes:
    title:        RADOLAN RW rainfall data
    source:       ftp://ftp-cdc.dwd.de/pub/CDC/grids_germany/hourly/radolan/
    institution:  DWD
    history:      Created at 2018-01-27 04:14:35.717004
    Conventions:  CF-1.6

# Plot the rainfall maps using `bokeh` 

In [4]:
from bokeh.plotting import figure, output_notebook, show
from bokeh.models import ColorBar, LinearColorMapper
from bokeh.models.tools import CustomJSHover, HoverTool
import pandas as pd

output_notebook()

Loading BokehJS ...

In [5]:
x_min = ds.x.values.min()
x_max = ds.x.values.max()
y_min = ds.y.values.min()
y_max = ds.y.values.max()
x_width = x_max - x_min
y_height = y_max - y_min

cm = LinearColorMapper(palette="Spectral11", low=0, high=10)

p = figure(
    x_range=(x_min, x_max), 
    y_range=(y_min, y_max),
    tooltips=[
        ("(x,y)", "($x{‘0,0’}, $y{‘0,0’})"),
        ("rainfall amount", "@image")
    ]
)

i = 10

im = p.image(
    image=[ds.rainfall_amount.isel(time=i).values],
    x=x_min, 
    y=y_min, 
    dw=x_width,
    dh=y_height,
    color_mapper=cm,
)
p.title.text = str(ds.time.isel(time=i).values)[:22]

# Helper function to plot outline of Germany (note that coordinates 
# have to be converte from meteres to kilometers)
df_shape_ger = pd.read_csv('shape_germany.csv', index_col=0)
for part, df_part in df_shape_ger.groupby('part'):
    p.line(
        df_part.x_dwd.values / 1e3,
        df_part.y_dwd.values / 1e3,
        line_width=2,
        line_color='black')

show(p)

# Add time slider using `bokeh.models.widgets`

It is important to note that `bokeh.models.widgets` do not work directly in the notebook because only `bokeh` server can execute Python callbacks. But there is a workaround. As [this notebook](https://github.com/bokeh/bokeh/blob/db8e23e96be271802c9ff9b164deabbbc29e52f4/examples/howto/server_embed/notebook_embed.ipynb) shows one can launch a `bokeh` server automatically in the background and embed its output in the notebook. You just have to wrap your `bokeh` code in a function that is then called by `show()` in the end.

In [6]:
from bokeh.plotting import figure, output_notebook, show
from bokeh.models import ColorBar, LinearColorMapper
from bokeh.models.tools import CustomJSHover, HoverTool

from bokeh.models.widgets import Slider
from bokeh.layouts import column

def app(doc):
    x_min = ds.x.values.min()
    x_max = ds.x.values.max()
    y_min = ds.y.values.min()
    y_max = ds.y.values.max()
    x_width = x_max - x_min
    y_height = y_max - y_min

    cm = LinearColorMapper(palette="Spectral11", low=0, high=20)

    p = figure(
        x_range=(x_min, x_max), 
        y_range=(y_min, y_max),
        tooltips=[
            ("(x,y)", "($x{‘0,0’}, $y{‘0,0’})"),
            ("rainfall amount", "@image")
        ]
    )

    i = 10

    im = p.image(
        image=[ds.rainfall_amount.isel(time=i).values],
        x=x_min, 
        y=y_min, 
        dw=x_width,
        dh=y_height,
        color_mapper=cm,
    )
    p.title.text = str(ds.time.isel(time=i).values)[:22]
    # Helper function to plot outline of Germany (note that coordinates 
    # have to be converte from meteres to kilometers)
    df_shape_ger = pd.read_csv('shape_germany.csv', index_col=0)
    for part, df_part in df_shape_ger.groupby('part'):
        p.line(
            df_part.x_dwd.values / 1e3,
            df_part.y_dwd.values / 1e3,
            line_width=2,
            line_color='black')
    
    def update_data(attr, old, new):
        #i = time_index.value
        im.data_source.data = {'image': [ds.rainfall_amount.isel(time=new).values]}
        p.title.text = str(ds.time.isel(time=new).values)[:22]

    time_slider = Slider(
        title="time_index", 
        value=0,
        start=0, 
        end=len(ds.time)-1, 
        step=1,
        callback_throttle=100
    )

    time_slider.on_change('value_throttled', update_data)
    
    doc.add_root(column(time_slider, p))
    
# NOTE: If the current notebook is not displayed at the 
#       default URL, you must pass the notebook_url parameter
show(app, notebook_url="http://localhost:8891")

# Open big weather radar data from KNMI via OPeNDAP

KNMI provides many data sets, including weather radar products via a THREDDS server which let's you access the data with OPeNDAP URLs. The KNIM THREDDS server is here
http://opendap.knmi.nl/knmi/thredds/catalog.html

Note that you have to add `'#fillmismatch'` to the Opendap URL because of some inconsistency with the fill value dtype

Rainfall amount per hour is given in the variable `image1_image_data`

**This data set has now approx. 220 GB**, which still sits at the KNMI server. But we can dynamically access it as we required.

In [7]:
ds = xr.open_dataset('http://opendap.knmi.nl/knmi/thredds/dodsC/radarprecipclim/RAD_NL25_RAC_MFBS_01H_NC.nc#fillmismatch')
ds

<xarray.Dataset>
Dimensions:             (time: 104432, x: 700, y: 765)
Coordinates:
  * y                   (y) float64 -3.65e+03 -3.652e+03 ... -4.414e+03
  * x                   (x) float64 0.5 1.5 2.5 3.5 ... 696.5 697.5 698.5 699.5
  * time                (time) datetime64[ns] 2008-01-01 ... 2019-11-30T07:00:00
Data variables:
    geographic          |S64 ...
    image1_calibration  |S64 ...
    overview            |S64 ...
    radar1              |S64 ...
    radar2              |S64 ...
    radar3              |S64 ...
    product             |S64 ...
    iso_dataset         |S64 ...
    projection          |S64 ...
    image1_image_data   (time, y, x) float32 ...
Attributes:
    _NCProperties:  version=1|netcdflibversion=4.4.1.1|hdf5libversion=1.8.20
    Conventions:    CF-1.5
    history:        Metadata adjusted by ADAGUC from KNMIHDF5 to NetCDF-CF
    DODS.strlen:    0

In [8]:
print('Size of data: %2.2f GB' % (ds.image1_image_data.nbytes/1e9))

Size of data: 223.69 GB


In [9]:
from bokeh.plotting import figure, output_notebook, show
from bokeh.models import ColorBar, LinearColorMapper
from bokeh.models.tools import CustomJSHover, HoverTool

from bokeh.models.widgets import Slider
from bokeh.layouts import column

def app(doc):
    x_min = ds.x.values.min()
    x_max = ds.x.values.max()
    y_min = ds.y.values.min()
    y_max = ds.y.values.max()
    x_width = x_max - x_min
    y_height = y_max - y_min

    cm = LinearColorMapper(palette="Spectral11", low=0, high=20)

    p = figure(
        x_range=(x_min, x_max), 
        y_range=(y_min, y_max),
        tooltips=[
            ("(x,y)", "($x{‘0,0’}, $y{‘0,0’})"),
            ("rainfall amount", "@image")
        ]
    )

    i = 10

    im = p.image(
        # Note: Thet data hast to be inverted along the y-axis
        image=[ds.image1_image_data.isel(time=i).values[-1::-1, :]],
        x=x_min, 
        y=y_min, 
        dw=x_width,
        dh=y_height,
        color_mapper=cm,
    )
    p.title.text = str(ds.time.isel(time=i).values)[:22]
    
    def update_data(attr, old, new):
        im.data_source.data = {'image': [ds.image1_image_data.isel(time=new).values[-1::-1, :]]}
        p.title.text = str(ds.time.isel(time=new).values)[:22]

    time_slider = Slider(
        title="time_index", 
        value=0,
        start=0, 
        end=len(ds.time)-1, 
        step=1,
        callback_throttle=500
    )

    time_slider.on_change('value_throttled', update_data)
    
    doc.add_root(column(time_slider, p))
    
show(app, notebook_url="http://localhost:8891")